In [11]:
%matplotlib widget

# AES in Python

The cryptography library tries to keep us safe but we want to see AES as a raw block cipher. To do this we want to use the "electronic codebook" (ECB) mode. To check if we are really getting the "raw" AES function we can compare outputs to the tests in [FIPS 197](https://nvlpubs.nist.gov/nistpubs/FIPS/NIST.FIPS.197.pdf): 

```
AES-128 example (key is 128 bits):
PLAINTEXT: 00112233445566778899aabbccddeeff
KEY: 000102030405060708090a0b0c0d0e0f
round[10].output 69c4e0d86a7b0430d8cdb78070b4c55a

AES-192 example (key is 192 bits)
PLAINTEXT: 00112233445566778899aabbccddeeff
KEY: 000102030405060708090a0b0c0d0e0f1011121314151617
round[12].output dda97ca4864cdfe06eaf70a0ec0d7191

AES-256 example (key is 256 bits)
PLAINTEXT: 00112233445566778899aabbccddeeff
KEY: 000102030405060708090a0b0c0d0e0f101112131415161718191a1b1c1d1e1f
round[14].output 8ea2b7ca516745bfeafc49904b496089
```


In [12]:
from cryptography.hazmat.primitives.ciphers import (Cipher, algorithms, modes)

## AES-128 test

In [2]:
plaintext = bytes.fromhex("00112233445566778899aabbccddeeff")
key = bytes.fromhex("000102030405060708090a0b0c0d0e0f")
encryptor = Cipher(algorithms.AES(key), modes.ECB()).encryptor()
ciphertext = encryptor.update(plaintext)
print(ciphertext.hex())
# Expected output: 69c4e0d86a7b0430d8cdb78070b4c55a

69c4e0d86a7b0430d8cdb78070b4c55a


In [3]:
decryptor = Cipher(algorithms.AES(key), modes.ECB()).decryptor()
dtext = decryptor.update(ciphertext)
print(dtext.hex())

00112233445566778899aabbccddeeff


## AES-192 Test

In [4]:
plaintext = bytes.fromhex("00112233445566778899aabbccddeeff")
key = bytes.fromhex("000102030405060708090a0b0c0d0e0f1011121314151617")
encryptor = Cipher(algorithms.AES(key), modes.ECB()).encryptor()
ciphertext = encryptor.update(plaintext)
print(ciphertext.hex())
# Expected output: dda97ca4864cdfe06eaf70a0ec0d7191

dda97ca4864cdfe06eaf70a0ec0d7191


In [5]:
decryptor = Cipher(algorithms.AES(key), modes.ECB()).decryptor()
dtext = decryptor.update(ciphertext)
print(dtext.hex())

00112233445566778899aabbccddeeff


## AES-256 Test

In [6]:
plaintext = bytes.fromhex("00112233445566778899aabbccddeeff")
key = bytes.fromhex("000102030405060708090a0b0c0d0e0f101112131415161718191a1b1c1d1e1f")
encryptor = Cipher(algorithms.AES(key), modes.ECB()).encryptor()
ciphertext = encryptor.update(plaintext)
print(ciphertext.hex())
# Expected output: 8ea2b7ca516745bfeafc49904b496089

8ea2b7ca516745bfeafc49904b496089


In [7]:
decryptor = Cipher(algorithms.AES(key), modes.ECB()).decryptor()
dtext = decryptor.update(ciphertext)
print(dtext.hex())

00112233445566778899aabbccddeeff


# Images in Python

To understand some of the security issues that can arise with inappropriate use of a **block cipher** we need a large data set to encrypt and we need that data set to have a fair amount of redundancy. Uncompressed images can meet this objective. 

So we will first look at the structure of uncompressed JPEG images with Python. First we will use the *matplotib.image* package to help us read in a JPEG image and look at its structure as a [numpy](https://numpy.org) array.

In [8]:
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import numpy as np

In [9]:
# I took a screenshot of the image tutorial page
img = mpimg.imread('test.jpg')

In [13]:
plt.figure()
plt.imshow(img)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [21]:
# Image information
print(f"The image size in bytes: {img.size}")
print(f"The number of dimensions in the image array: {img.ndim}")
print(f"The size of each image dimension: {img.shape}")
print(f"The type of data in the image arra: {img.dtype}")

The image size in bytes: 3117102
The number of dimensions in the image array: 3
The size of each image dimension: (739, 1406, 3)
The type of data in the image arra: uint8


**Interpretation**: This image has a height of 739 pixels and a width of 1406 pixels. Each pixel's color is specified by a combination of three bytes (the third dimension is color) one each for Red, Green, and Blue.

# Raw AES Block Cipher Usage

As a block cipher AES works on 128 bits (16 bytes) at a time so to encrypt our uncompressed image array we will need to group together 16 bytes at a time. In our encryptor function shown below we group 4x4 blocks of pixels and encrypt each color separately to get a block of 128 bits. In other words we are encrypting 4x4 blocks of pixels in each color plane. 

Note that one would typically encrypt compress image files, however our purpose here is to show that inappropriate block cipher usage will result in data leakage, i.e., loss of confidentiality.


In [16]:
# Set up encryptor and decryptor
key = bytes.fromhex("000102030405060708090a0b0c0d0e0f")
encryptor = Cipher(algorithms.AES(key), modes.ECB()).encryptor()
decryptor = Cipher(algorithms.AES(key), modes.ECB()).decryptor()

In [17]:
def jpgEncrypt(npimg, encrypt=True):
    shape = npimg.shape
    # Chop off rows and columns to be a multiple of 4
    nshape = ((shape[0]//4)*4, (shape[1]//4)*4, shape[2])
    cimg = np.ndarray(nshape, np.uint8)
    # Encrypt by block
    for i in range(0, nshape[0]//4):
        for j in range(0, nshape[1]//4):
            for k in range(0, 3):
                mybytes = npimg[4*i:4*(i + 1), 4*j:4*(j+1), k].tobytes()
                if encrypt:
                    cbytes = encryptor.update(mybytes)
                else:
                    cbytes = decryptor.update(mybytes)
                deserialized_bytes = np.frombuffer(cbytes, dtype=np.uint8)
                cimg[4*i:4*(i + 1), 4*j:4*(j+1), k] = np.reshape(deserialized_bytes, newshape=(4, 4))
    return cimg
    

In [18]:
# Encrypt the image
cimg = jpgEncrypt(img)
# mpimg.imsave("ECBtest.jpg", cimg)

In [19]:
# Decrypt the image -- to show that we can
cimg2 = jpgEncrypt(cimg, False)

In [20]:
plt.figure()
plt.imshow(cimg)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [22]:
plt.figure()
plt.imshow(cimg2)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

# An Appropriate AES Mode

A more appropriate block cipher mode of operation for this task is known as [Cipher Block Chaining](https://en.wikipedia.org/wiki/Block_cipher_mode_of_operation#Cipher_block_chaining_(CBC). In this mode the ciphertext from a previous iteration is combined with the plaintext for the next iteration, i.e.,

$$ C_{i}=E_{K}(P_{i}\oplus C_{i-1})$$
$$C_{0}=IV$$

To start the process off an [*initialization vector*](https://en.wikipedia.org/wiki/Initialization_vector) (IV) is required. These IV have requirements that can vary by the mode.

In [23]:
# Set up encryptor and decryptor
key = bytes.fromhex("000102030405060708090a0b0c0d0e0f")
# Need to set the initialization vetor
iv = bytes.fromhex("e0e1e2f3f4a5a6a7b8b90a0b0c0d0e0f")
encryptor = Cipher(algorithms.AES(key), modes.CBC(iv)).encryptor()
decryptor = Cipher(algorithms.AES(key), modes.CBC(iv)).decryptor()

In [24]:
cbcimg = jpgEncrypt(img)

In [25]:
#mpimg.imsave("CBCtest.jpg", cbcimg)

In [26]:
plt.figure()
plt.imshow(cbcimg)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [27]:
dcbcimg = jpgEncrypt(cbcimg, encrypt=False)

In [28]:
plt.figure()
plt.imshow(dcbcimg)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …